In [5]:
import mysql.connector
import json
import pandas as pd
from tqdm.notebook import tqdm
from datetime import datetime
import re
import numpy as np
from openai import OpenAI

In [6]:
client = OpenAI()

OpenAIError: The api_key client option must be set either by passing api_key to the client or by setting the OPENAI_API_KEY environment variable

In [7]:
with open("../crawling/tokens.json") as f:
    passwords = json.load(f)

pwd=passwords["mysql_password"]

In [8]:
# Connect to MySQL
connection = mysql.connector.connect(
    host='localhost',
    user='root',
    password=pwd,
    database='stampcollection'
)

cursor = connection.cursor()

InterfaceError: 2003: Can't connect to MySQL server on 'localhost:3306' (Errno 10061: Es konnte keine Verbindung hergestellt werden, da der Zielcomputer die Verbindung verweigerte)

In [9]:
df = pd.read_csv('../crawling/contents_merged/all_contents_updated_2.csv')

C:\Users\Robin\AppData\Local\Temp\ipykernel_31200\2775233162.py:1: DtypeWarning: Columns (13,16,21) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('../crawling/contents_merged/all_contents_updated_2.csv')


# Edit the df to fit in the db later

In [10]:
def parse_date(date_str):
    if pd.isna(date_str):  # Check for NaN values
        return None
    try:
        # Try to parse the date in the format %d/%m/%Y
        return datetime.strptime(date_str, '%d/%m/%Y').strftime('%Y-%m-%d')
    except ValueError:
        try:
            # Try to parse the date in the format %Y
            return datetime.strptime(date_str, '%Y').strftime('%Y-01-01')
        except ValueError:
            try:
                # Handle the format MM//YYYY by assuming the first day of the month
                return datetime.strptime(date_str, '%m//%Y').strftime('%Y-%m-%d')
            except ValueError:
                # Print the date string that couldn't be parsed if it's not NaN
                print(f"Couldn't parse: {date_str}")
                # Return None if the date cannot be parsed
                return None

# Convert the date format in the DataFrame
df['Date_of_Issue'] = df['Date_of_Issue'].apply(parse_date)

In [ ]:
# # Create a new table
# # drop table if exists
# cursor.execute("DROP TABLE IF EXISTS contents")
# create_table_query = """
# CREATE TABLE contents (
#     Country VARCHAR(255),
#     Category VARCHAR(255),
#     Year INT,
#     Set_Url VARCHAR(255),
#     Set_Name TEXT,
#     Set_ID VARCHAR(255),
#     Set_Description TEXT,
#     Number VARCHAR(255),
#     Type VARCHAR(10),
#     Denomination VARCHAR(255),
#     Color VARCHAR(255),
#     Description TEXT,
#     Stamps_Issued VARCHAR(255),
#     Mint_Condition VARCHAR(255),
#     Unused VARCHAR(255),
#     Used VARCHAR(255),
#     `Letter/FDC` VARCHAR(255),
#     Currency VARCHAR(10),
#     Image_URL VARCHAR(255),
#     Date_of_Issue DATE,
#     Perforations VARCHAR(255),
#     Sheet_Size VARCHAR(255),
#     Design VARCHAR(255),
#     Engraved_By VARCHAR(255),
#     Height_Width VARCHAR(255),
#     Themes TEXT,
#     Image_Accuracy INT
# )
# """
# cursor.execute(create_table_query)

# clear table
cursor.execute("TRUNCATE TABLE contents")

# Insert data into the table
for i, row in tqdm(df.iterrows(), total=df.shape[0]):
    insert_row_query = """
    INSERT INTO contents (Country, Category, Year, Set_Url, Set_Name, Set_ID, Set_Description, Number, Type, Denomination, Color, Description, Stamps_Issued, Mint_Condition, Unused, Used, `Letter/FDC`, Currency, Image_URL, Date_of_Issue, Perforations, Sheet_Size, Design, Engraved_By, Height_Width, Themes, Image_Accuracy)
    VALUES (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)
    """
    cursor.execute(insert_row_query, tuple(row))
    connection.commit()

# Close the connection
cursor.close()
connection.close()


# check if database if complete

In [8]:
# get number of rows in table
cursor.execute("SELECT COUNT(*) FROM contents")
print(cursor.fetchall())
print(df.shape[0])

[(1063560,)]
1063560


# Add some columns for easier access


## Add a column for perforaations

The column should contain float numers

In [85]:
# make copy of df
df_copy = df.copy()

In [35]:
# list all unique values in Perforation column
unique_perforations = df_copy['Perforations'].unique()
# print ALL unique values
for perforation in unique_perforations:
    print(perforation)

Imperforated
14¼
nan
11
13
14
11¾
12¾
13 x 13¼
13¼ x 13¾
13¾
13 x 12¾
12¼
14 on 3 sides
13½ x 12¾
13 x 14
14 on three sides
12¾ on three sides
13¾ x 13¼
12¾ x 14
14 x 12¾
12¾ x 13
14½ x 14¾
14¾ x 14½
14 x 14½
11¾ on three sides
13½ x 13¼
12¾ x 13¼
13¼ on 3 sides
14½ x 13¾
13¾ x 14¼
13¼
12½
13½
12¾ x 13½
12½ x 12¾
13½ x 13
Rouletted 8
14¾ x 14¼
14¼ x 14¾
10½
12½ x 13
Rouletted 11
13 top and bottom
Rouletted 10
14 x 13
13 horizontally
12
10
121.2
11½
11¾ and 11½
11¼
14½
13 x 13½
14½ and 13 x 13½
14½ x 14
14 x 13½
13 x 11½
13½ x 14
13½ and 11 x 11½
12 x 13½
12¼ x 12¾
12 x 12½
13 x 12½
11 or 12
Zigzag Rouledded 10
11 on 2 or 3 sides
11 x 12
11-12
12 or 12 x 11
11-11½
12-13½
11 & 12
13½ x 14¼
14¼ x 13½
13 x 12
11½ x 12
12 or imperforated
12 x 11
13½ x 12
1
11 x 10½
10½ x 11
12½ x 12
12 x 11½
12-12½
12½ x 12¼
12¼ x 12½
12 x 13
36
Rouletted
13¼ x 13
13 - 14½
14 x 15
14 x 13½ & 14 x 14½
13 x 14½
14 x 13¾
13¾ x 13
13¾ x 13½
14 x 14¼
14½ x 13
14¼ x 13¾
14¼ x 14
14¼ x 13
13¼ x 12¾
14¾
14 x 14¾
41

In [36]:
pattern1 = r"^\d+(¼|½|⅓|⅔|¼|¾)?( )+x( )+\d+(¼|½|⅓|⅔|¼|¾)?$"
pattern2 = r"^\d+(¼|½|⅓|⅔|¼|¾)?$"

# for vertical, vertically horizontal, horizontally
# pattern3 = r"^\d+(¼|½|⅓|⅔|¼|¾)? horizontally$"
pattern3 = r"^\d+(¼|½|⅓|⅔|¼|¾)? ((h|H)orizontally|(h|H)orizontal)$"
pattern6 = r"^\d+(¼|½|⅓|⅔|¼|¾)? ((v|V)ertically|(v|V)ertical)$"

pattern4 = r"^\d+(¼|½|⅓|⅔|¼|¾)?( )?(,|:|;|and|&|or|-|х|X)( )?\d+(¼|½|⅓|⅔|¼|¾)?$"
pattern5 = r".*\d+(¼|½|⅓|⅔|¼|¾)? x \d+(¼|½|⅓|⅔|¼|¾)?.*"


horizontal = [] # first  number (width)
vertical   = [] # second number (height)
keyword    = [] # a keyword regarding the perforation

# set first true if after x and false if before x
def getNumberFromString(string, first = True):
    
    fraction_map = { 
        '½': 0.5, 
        '⅓': 1/3, 
        '⅔': 2/3, 
        '¼': 0.25, 
        '¾': 0.75 
    }

    # split at " " and get first or last depending on first
    string = string.split(' ')[0] if first else string.split(' ')[-1]

    # Remove any non-numeric characters
    fraction_str = re.sub(r'[^\d½⅓⅔¼¾]+', '', string)
    
    # Split the string into integer and fractional parts
    for frac in fraction_map:
        if frac in fraction_str:
            parts = fraction_str.split(frac)
            integer_part = int(parts[0]) if parts[0] else 0
            fractional_part = fraction_map[frac]
            return integer_part + fractional_part
    
    # If no fractional part is found, return the integer part
    return int(fraction_str)

# apply this for all elements in unique_perforations
for perforation in unique_perforations:
    keywords = []

    perforation = str(perforation)

    # replace some specific terms
    # replace 121.2 with 12½
    perforation = perforation.replace('133/5', '13½')
    perforation = perforation.replace('133/3', '13½')
    perforation = perforation.replace('13/¼', '13¼')
    perforation = perforation.replace('14/½', '14½')
    perforation = perforation.replace('121.2', '12½')
    perforation = perforation.replace('Imperfoarted', 'Imperforated')
    perforation = perforation.replace('Imperforted', 'Imperforated')
    perforation = perforation.replace('x14', 'x 14')
    perforation = perforation.replace('133/¤', '13¾')
    perforation = perforation.replace('121/12', '12')
    perforation = perforation.replace('131/ ', '13½ ')
    perforation = perforation.replace('13½n', '13½')
    perforation = perforation.replace('13¾ x x13½', '13¾ x 13½')
    perforation = perforation.replace('top and bottom', 'horizontally')
    if(perforation == "¼ ½"):
        perforation = perforation.replace('¼ ½', '')

    # if perforation includes Imperforated make keyword Imperforated
    if 'Imperforated' in perforation or 'imperforated' in perforation or 'Imperforate' in perforation:
        keywords.append('Imperforated')
    if 'Printed' in perforation:
        keywords.append('Printed')
    if ' on 3 sides' in perforation or ' on three sides' in perforation:
        keywords.append('3 sides')
    if ' on 2 sides' in perforation or ' on two sides' in perforation:
        keywords.append('2 sides')
    if 'on 2 or 3 sides' in perforation:
        keywords.append('2 or 3 sides')
    if 'on 3 or 4 sides' in perforation:
        keywords.append('3 or 4 sides')
    if 'Zigzag Rouledded' in perforation:
        keywords.append('Zigzag Rouledded')
    if any(term in perforation.lower() for term in ['rouletted', 'roulette']):
        keywords.append('Rouletted')
    if perforation.lower() == "printed":
        keywords.append('Printed')
    if perforation.lower() == "different":
        keywords.append('Different')
    if perforation.lower() == "die cut" or perforation.lower() == "diecut":
        keywords.append('Die Cut')
    if perforation.lower() == "laser die cut":
        keywords.append('Laser Die Cut')
    if perforation.lower() == "laser-cut":
        keywords.append('Laser Cut')
    if perforation.lower() == "rough":
        keywords.append('Rough')
    if perforation.lower() == "wavy":
        keywords.append('Wavy')
    if perforation.lower() == "simulated":
        keywords.append('Simulated')
    if perforation.lower() == "cut":
        keywords.append('Cut')

    perforation = perforation.replace('11 or Rouletted', '11').strip()
    perforation = perforation.replace('/Printed', '').strip()

    # remove three sides
    perforation = perforation.replace(' on three sides', '').strip()
    perforation = perforation.replace(' on 3 sides', '').strip()
    perforation = perforation.replace(' on two sides', '').strip()
    perforation = perforation.replace(' on 2 sides', '').strip()
    perforation = perforation.replace(' on 2 or 3 sides', '').strip()
    perforation = perforation.replace(' on 3 or 4 sides', '').strip()
    # remove rouletted
    perforation = perforation.replace('rouletted', '').strip()
    perforation = perforation.replace('roulette', '').strip()
    perforation = perforation.replace('Rouletted', '').strip()
    perforation = perforation.replace('Roulette', '').strip()
    # remove imperforated
    perforation = perforation.replace('or imperforated', '').strip()
    perforation = perforation.replace('or Imperforated', '').strip()
    perforation = perforation.replace('Imperforated', '').strip()
    perforation = perforation.replace('imperforated', '').strip()
    perforation = perforation.replace('Imperforate', '').strip()

    # remove Zigzag Rouledded
    perforation = perforation.replace('Zigzag Rouledded', '').strip()
    # remove different
    perforation = perforation.replace('Different', '').strip()
    perforation = perforation.replace('different', '').strip()
    # remove die cut
    # remove laser die cut
    perforation = perforation.replace('Laser Die Cut', '').strip()
    perforation = perforation.replace('Laser-cut', '').strip()
    perforation = perforation.replace('Die Cut', '').strip()
    perforation = perforation.replace('Diecut', '').strip()
    perforation = perforation.replace('Cut', '').strip()
    perforation = perforation.replace('Rough', '').strip()
    perforation = perforation.replace('Wavy', '').strip()
    perforation = perforation.replace('Simulated', '').strip()

    if re.match(pattern3, perforation):
        keywords.append('Just Horizontal')
    if re.match(pattern6, perforation):
        keywords.append('Just Vertical')

    if re.match(pattern1, perforation):
        splitted = perforation.split(' x ')
        horizontal.append(getNumberFromString(splitted[0].strip(), first = False))
        vertical.append(getNumberFromString(splitted[1].strip(), first = True))
    elif re.match(pattern4, perforation):
        splitted = re.split(r'(:|,|;|and|&|or|-|х|X)', perforation)
        horizontal.append(getNumberFromString(splitted[0].strip(), first = False))
        vertical.append(getNumberFromString(splitted[2].strip(), first = True))
    elif re.match(pattern2, perforation):
        horizontal.append(getNumberFromString(perforation, first = True))
        vertical.append(getNumberFromString(perforation, first = True))
    elif re.match(pattern3, perforation):
        perforation = perforation.replace(' horizontally', '').strip()
        perforation = perforation.replace(' Horizontally', '').strip()
        perforation = perforation.replace(' horizontal', '').strip()
        perforation = perforation.replace(' Horizontal', '').strip()
        horizontal.append(getNumberFromString(perforation, first = True))
        vertical.append(None)
    elif re.match(pattern6, perforation):
        perforation = perforation.replace(' vertically', '').strip()
        perforation = perforation.replace(' Vertically', '').strip()
        perforation = perforation.replace(' vertical', '').strip()
        perforation = perforation.replace(' Vertical', '').strip()
        vertical.append(getNumberFromString(perforation, first = True))
        horizontal.append(None)
    
    elif re.match(pattern5, perforation):
        # should be last elif
        keywords.append('Multiple Perforations')
        # get first occurance of pattern
        splitted = re.findall(r'\d+(?:¼|½|⅓|⅔|¼|¾)? x \d+(?:¼|½|⅓|⅔|¼|¾)?', perforation)[0]
        splitted = re.split(r'(x|;|and|&|or|-|х)', splitted)
        horizontal.append(getNumberFromString(splitted[0].strip(), first = False))
        vertical.append(getNumberFromString(splitted[2].strip(), first = True))
    elif perforation.lower() == 'nan' or pd.isna(perforation) or perforation == '' or perforation.lower() == 'printed' or perforation.lower() == 'laser die cut':
        horizontal.append(None)
        vertical.append(None)
    else:
        horizontal.append("not implemented yet")
        vertical.append("not implemented yet")

    keyword.append(keywords)

# make a df of this and print the entire df
df_perforations = pd.DataFrame({'Perforations': unique_perforations, 'Horizontal': horizontal, 'Vertical': vertical, 'Keyword': keyword})
# Set display option to show all rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)  # Prevents wrapping of columns

print(df_perforations)

# Reset display option to default
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')
pd.reset_option('display.expand_frame_repr')

# # loop over all values in the Perforations column
# for perforation in perfortions:
#     # check if the value matches the pattern
#     if re.match(pattern1, perforation):
#         splitted = perforation.split(' x ')
#         # convert the 

                                           Perforations           Horizontal             Vertical                                Keyword
0                                          Imperforated                 None                 None                         [Imperforated]
1                                                   14¼                14.25                14.25                                     []
2                                                   NaN                 None                 None                                     []
3                                                    11                   11                   11                                     []
4                                                    13                   13                   13                                     []
5                                                    14                   14                   14                                     []
6                                        

In [37]:
# get row where Perforations includes 131/
df_copy[df_copy['Perforations'].fillna('').str.contains('133/3')]["Set_Url"].iloc[0]

'https://www.stampworld.com/stamps/Argentina/Postage-stamps/g1480//'

### merge dfs

In [38]:
# Merge the dataframes
df_merged = pd.merge(df_copy, df_perforations, on='Perforations', how='left')


In [39]:
all_horizontal = df_merged['Horizontal']

In [40]:
count_not_implemented = np.count_nonzero(all_horizontal == "not implemented yet")
count_none =  np.count_nonzero(all_horizontal.isnull())
print(count_not_implemented / len(all_horizontal))
print(count_none / len(all_horizontal))
print(1 - (count_not_implemented + count_none) / len(all_horizontal))

0.007708074767761104
0.27097954041144834
0.7213123848207905


# Denomination

In [41]:
# list all unique values in Perforation column
unique_denominations = df_copy['Denomination'].unique()
# print ALL unique values
for denomination in unique_denominations:
    print(denomination)

10-9890P
10-9900P
0.10-99.90mk.
0.01-99.95€
0.01-99.99€
nan
0.20mk.
0.50mk.
1.10mk.
1.40mk.
3.00mk.
10.00mk.
2.00mk.
1.50mk.
0.10mk.
1.20mk.
5.00mk.
8.00mk.
1.30mk.
1.60mk.
2.20mk.
20.00mk.
3.70mk.
1.70mk.
2.30mk.
12.00mk.
7.00mk.
1.00mk.
1.80mk.
2.40mk.
11.00mk.
1.90mk.
2.50mk.
14.00mk.
2.70mk.
13.00mk.
2.10mk.
2.90mk.
16.00mk.
1klasse
2klasse
3.40mk.
3.50mk.
17.00mk.
6.00mk.
2.80mk.
18.00mk.
4.30mk.
0.40mk.
9.00mk.
0.30mk.
4.20mk.
6.30mk.
2.90/0.49mk./€
3.40/0.57mk./€
1.80/0.30mk./€
2.20/0.37mk./€
2.60/0.44mk./€
3.00/0.50mk./€
4.50/0.76mk./€
3.80/0.64mk./€
10.00/1.68mk./€
2.00/0.34mk./€
1.90/0.32mk./€
2.80/0.47mk./€
3.50/0.59mk./€
2.70/0.45mk./€
3.20/0.54mk./€
7.00/1.18mk./€
20.00/3.36mk./€
0.60€
0.05€
0.70€
2.00€
1.00€
3.00€
0.40€
0.90€
0.35€
0.10€
0.50€
2.50€
0.45€
0.55€
1.10€
0.20€
0.75€
0.80€
0.15€
0.65€
4.00€
1.30€
0.85€
1.50€
1.20€
JULPOST
5.00€
4.50€
VARLDEN
INRIKES
EUROPA
2.00EUROPA
0.80EUROPA
1.60€
3.50€
LOKALPOST
1.80€
1.00+0.20 €
1.10+0.20 €
2.30€
10.00€
1.40€
1.70€
6.00€


In [42]:
# unique value pattern (including .)
pattern1 = r"\d+(\.\d+)?-\d+(\.\d+)?"
pattern2 = r"\d+(\.\d+)?"

# get numbers from denomination
denomination_value_from = []
denomination_value_to = []

for denomination in unique_denominations:
    denomination = str(denomination)

    # ½ to .5
    if denomination.startswith('½'):
        denomination = denomination.replace('½', '0.5', 1)
    denomination = denomination.replace('½', '.5')

    if re.match(pattern1, denomination) and denomination.count('-') == 1:
        match = re.search(pattern1, denomination)
        splitted = match.group().split('-')
        denomination_value_from.append(float(splitted[0]))
        denomination_value_to.append(float(splitted[1]))
    elif re.match(pattern2, denomination):
        match = re.search(pattern2, denomination)
        # print(match.group())
        denomination_value_from.append(float(match.group()))
        denomination_value_to.append(float(match.group()))
    else:
        denomination_value_from.append(0)
        denomination_value_to.append(0)

# make a df of this and print the entire df
df_denominations = pd.DataFrame({'Denomination': unique_denominations, 'Value_From': denomination_value_from, 'Value_To': denomination_value_to})

# Set display option to show all rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)  # Prevents wrapping of columns

print(df_denominations)

# Reset display option to default
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')
pd.reset_option('display.expand_frame_repr')

                        Denomination    Value_From      Value_To
0                           10-9890P  1.000000e+01  9.890000e+03
1                           10-9900P  1.000000e+01  9.900000e+03
2                      0.10-99.90mk.  1.000000e-01  9.990000e+01
3                        0.01-99.95€  1.000000e-02  9.995000e+01
4                        0.01-99.99€  1.000000e-02  9.999000e+01
5                                NaN  0.000000e+00  0.000000e+00
6                            0.20mk.  2.000000e-01  2.000000e-01
7                            0.50mk.  5.000000e-01  5.000000e-01
8                            1.10mk.  1.100000e+00  1.100000e+00
9                            1.40mk.  1.400000e+00  1.400000e+00
10                           3.00mk.  3.000000e+00  3.000000e+00
11                          10.00mk.  1.000000e+01  1.000000e+01
12                           2.00mk.  2.000000e+00  2.000000e+00
13                           1.50mk.  1.500000e+00  1.500000e+00
14                       

In [43]:
# check if "35.6-456.6" matches pattern1
import re
match = re.search(pattern2, "(0.46)€")
if match:
    print(match.group())

0.46


In [44]:
# get row where Perforations includes 131/
df_copy[df_copy['Denomination'].fillna('').str.contains('LOKALPOST')]["Set_Url"].iloc[0]

'https://www.stampworld.com/stamps/Aaland/Postage-stamps/g0344//'

In [45]:
df_merged_2 = pd.merge(df_merged, df_denominations, on='Denomination', how='left')

In [23]:
df_merged_2.iloc[0]

Country                                                       Aaland
Category                                             Franking labels
Year                                                            1984
Set_Url            https://www.stampworld.com/stamps/Aaland/Frank...
Set_Name                                         1984 Franking Label
Set_ID                                                        256031
Set_Description       29. October WM: None Perforation: Imperforated
Number                                                             1
Type                                                               A
Denomination                                                10-9890P
Color                                                   brownish red
Description                                                      NaN
Stamps_Issued                                                    NaN
Mint_Condition                                                  1.50
Unused                            

# Color

In [24]:
# list all unique values in Perforation column
unique_colors = df_copy['Color'].unique()
# print ALL unique values
all_unique_colors = []
for color in unique_colors:
    color = str(color)
    for c in color.split('/'):
        all_unique_colors.append(c.strip())

all_unique_colors = list(set(all_unique_colors))

print(all_unique_colors)

['', 'black', 'orange red', 'brick-red', 'violet rose', 'steel blue', 'deep grey', 'deep reddish brown', 'dull yellowish green', 'greyish blue', 'greyish ultramarine', 'dull brownish red', 'dark violet', 'Maroon', 'dark lake', 'bluish purple', 'brown', 'dull carmine', 'orange yellow', 'copper brown', 'chrome yellow', 'hazel brown', 'silver', 'deep claret', 'greenish grey', 'purple rose', 'white', 'dark brown', 'pink', 'brownish purple', 'mauve grey', 'brownish red', 'dark pink', 'dark bluish green', 'purple carmine', 'dark purple', 'yellow', 'dull purple', 'greyish red', 'rose violet', 'dull pink', 'brownish blue', 'violet red', 'dull chocolate brown', 'blackish olive', 'blackish purple', 'reddish', 'blackish grey', 'brownish lake', 'greenish blue', 'yellowish brown', 'black on purple red', 'lemon-yellow', 'chestnut brown', 'indigo', 'yellowish ocher', 'pink purple', 'dull lilac', 'light bluish green', 'carmine violet', 'deep red', 'dark turquoise', 'reddish brown', 'greenish', 'bronce

In [21]:
# get general color
general_colors = []


for color in all_unique_colors:
    if(color == ''):
        general_colors.append([''])
        continue
    # ask openai
    input_text = f"Which general color/s (one of 'Red', 'Blue', 'Yellow', 'Orange', 'Green', 'Purple', 'White', 'Black') describes this color best: {color}?"
    completion = client.chat.completions.create(
        model="gpt-4o",
        messages=[
            {"role": "system", "content": "answer very shortly with one word. And you have to decide for one of the provided choices."},
            {
                "role": "user",
                "content": input_text
            }
        ]
    )

    response = completion.choices[0].message.content
    
    # split at ,
    general_colors.append(response.split(','))

# make df
df_colors = pd.DataFrame({'Color': all_unique_colors, 'General_Color': general_colors})

# Set display option to show all rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)  # Prevents wrapping of columns

print(df_colors)

# Reset display option to default
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')
pd.reset_option('display.expand_frame_repr')

                     Color    General_Color
0                                        []
1              carmine red           [Red.]
2     dark yellowish green          [Green]
3       deep reddish brown            [Red]
4                deep grey          [Black]
5          chocolate brown          [Black]
6              deep claret            [Red]
7             dull emerald          [Green]
8        dark bluish green          [Green]
9            prussian blue           [Blue]
10             silver-grey          [White]
11              orange red            [Red]
12             light green          [Green]
13                  violet         [Purple]
14           blackish blue           [Blue]
15           greyish black          [Black]
16               brick-red            [Red]
17          black on green          [Black]
18        dark olive green          [Green]
19              dull green          [Green]
20         yellowish olive          [Green]
21              rust brown      

In [22]:
# get first element of general color
df_colors['General_Color'] = df_colors['General_Color'].apply(lambda x: x[0])
# remove . from color in df_colors
df_colors['General_Color'] = df_colors['General_Color'].str.replace('.', '')


# Set display option to show all rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)  # Prevents wrapping of columns

print(df_colors)

# Reset display option to default
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')
pd.reset_option('display.expand_frame_repr')

                     Color  General_Color
0                                        
1              carmine red            Red
2     dark yellowish green          Green
3       deep reddish brown            Red
4                deep grey          Black
5          chocolate brown          Black
6              deep claret            Red
7             dull emerald          Green
8        dark bluish green          Green
9            prussian blue           Blue
10             silver-grey          White
11              orange red            Red
12             light green          Green
13                  violet         Purple
14           blackish blue           Blue
15           greyish black          Black
16               brick-red            Red
17          black on green          Black
18        dark olive green          Green
19              dull green          Green
20         yellowish olive          Green
21              rust brown         Orange
22          blackish olive        

In [23]:
# go through all rows of df_merged_2 and get the general colors and add them in a new column
df_merged_3 = df_merged_2.copy()
general_colors = []
for i, row in tqdm(df_merged_3.iterrows(), total=df_merged_3.shape[0]):
    color = row['Color']
    if(pd.isna(color)):
        general_colors.append([''])
        continue
    color = str(color)
    colors = color.split('/')
    general_color = []
    for c in colors:
        general_color.append(df_colors[df_colors['Color'] == c]['General_Color'].values[0])
    general_colors.append(general_color)
general_colors

  0%|          | 0/1063560 [00:00<?, ?it/s]

[['Red'],
 ['Purple'],
 ['Purple'],
 ['Purple'],
 ['Purple'],
 ['Purple'],
 ['Purple'],
 ['Purple'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 [''],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 [''],
 [''],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 [''],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 ['Multicoloured'],
 [''],
 ['Green'],
 ['Green'],
 ['Blue'],
 [''],
 ['Multicoloured'],
 ['Multicoloured'],
 [

In [24]:
df_merged_3["General_Colors"] = general_colors

In [25]:
df_merged_3.iloc[0]

Country                                                       Aaland
Category                                             Franking labels
Year                                                            1984
Set_Url            https://www.stampworld.com/stamps/Aaland/Frank...
Set_Name                                         1984 Franking Label
Set_ID                                                        256031
Set_Description       29. October WM: None Perforation: Imperforated
Number                                                             1
Type                                                               A
Denomination                                                10-9890P
Color                                                   brownish red
Description                                                      NaN
Stamps_Issued                                                    NaN
Mint_Condition                                                  1.50
Unused                            

# Stamps_Issued

In [ ]:
# list all unique values in Perforation column
unique_issues = df_copy['Stamps_Issued'].unique()

issues_numbers = []
for issue in unique_issues:

    if(pd.isna(issue)):
        issues_numbers.append(None)
        continue
    if issue == "(unbekannt)":
        issues_numbers.append(None)
        continue

    original = issue

    issue = issue.replace("(0,911,000 mill)", "91100")
    issue = issue.replace("(.)", "1000000")

    issue = str(issue).strip()

    # replace ( with ""
    issue = issue.replace("(", "")
    issue = issue.replace(")", "")

    if "mill" in issue:
        issue = issue.replace("mill", "")
        issue = issue.replace(",", ".")
        # convert to float
        issue = float(issue) * 1000000
    elif "bill" in issue:
        issue = issue.replace("bill", "")
        issue = issue.replace(",", ".")
        # convert to float
        issue = float(issue) * 1000000000
    else:
        issue = issue.replace(",", "")
        issue = issue.replace(".", "")

        # remove all non numeric characters
        issue = re.sub(r'[^\d]+', '', issue)
        # convert to float
        try: 
            issue = float(issue)
        except:
            print(original)
            # raise error
            raise ValueError("Could not convert to float")

    issues_numbers.append(str(int(issue)))

# create df
df_issues = pd.DataFrame({'Stamps_Issued': unique_issues, 'Number_Issued': issues_numbers})

# Set display option to show all rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)  # Prevents wrapping of columns

print(df_issues)

# Reset display option to default
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')
pd.reset_option('display.expand_frame_repr')


                              Stamps_Issued   Number_Issued
0                                       NaN            None
1                                  (2 mill)         2000000
2                                (1,5 mill)         1500000
3                                  (3 mill)         3000000
4                                  (1 mill)         1000000
5                                  (500000)          500000
6                                (1,2 mill)         1200000
7                                  (800000)          800000
8                                  (700000)          700000
9                                 (1100000)         1100000
10                                 (600000)          600000
11                              (2.000.000)         2000000
12                                (1000000)         1000000
13                                 (400000)          400000
14                                 (550000)          550000
15                                 (6500

In [26]:
# find the row where Stamps_Issued includes "0.911.000 "
df_copy[df_copy['Stamps_Issued'].fillna('').str.contains('(.)', regex = False)]["Set_Url"].iloc[0]

'https://www.stampworld.com/stamps/Taiwan/Postage-stamps/g3213//'

In [ ]:
# merge with df_merged_3
df_merged_4 = pd.merge(df_merged_3, df_issues, on='Stamps_Issued', how='left')

In [29]:
df_merged_4.iloc[0]

Country                                                       Aaland
Category                                             Franking labels
Year                                                            1984
Set_Url            https://www.stampworld.com/stamps/Aaland/Frank...
Set_Name                                         1984 Franking Label
Set_ID                                                        256031
Set_Description       29. October WM: None Perforation: Imperforated
Number                                                             1
Type                                                               A
Denomination                                                10-9890P
Color                                                   brownish red
Description                                                      NaN
Stamps_Issued                                                    NaN
Mint_Condition                                                  1.50
Unused                            

# Mint_Condition, Unused, Used, Letter/FDC

In [ ]:
# list all unique values in Perforation column
unique_perforations = df_copy['Mint_Condition'].unique()
# print ALL unique values
for perforation in unique_perforations:
    print(perforation)

In [53]:
unique_mint_condition = df_copy['Mint_Condition'].unique()
unique_unused = df_copy['Unused'].unique()
unique_used = df_copy['Used'].unique()
unique_letter_fdc = df_copy['Letter/FDC'].unique()

In [60]:
# convert allto float
unique_mint_condition_as_float = []
unique_unused_as_float = []
unique_used_as_float = []
unique_letter_fdc_as_float = []

for mint_condition in unique_mint_condition:
    mint_condition = str(mint_condition)
    if mint_condition == "nan":
        unique_mint_condition_as_float.append(None)
        continue
    mint_condition = mint_condition.replace(",", "")
    try:
        unique_mint_condition_as_float.append(float(mint_condition))
    except:
        print(mint_condition)

for unused in unique_unused:
    unused = str(unused)
    if unused == "nan":
        unique_unused_as_float.append(None)
        continue
    unused = unused.replace(",", "")
    try:
        unique_unused_as_float.append(float(unused))
    except:
        print(unused)

for used in unique_used:
    used = str(used)
    if used == "nan":
        unique_used_as_float.append(None)
        continue
    used = used.replace(",", "")
    try:
        unique_used_as_float.append(float(used))
    except:
        print(used)

for letter_fdc in unique_letter_fdc:
    letter_fdc = str(letter_fdc)
    if letter_fdc == "nan":
        unique_letter_fdc_as_float.append(None)
        continue
    letter_fdc = letter_fdc.replace(",", "")
    try:
        unique_letter_fdc_as_float.append(float(letter_fdc))
    except:
        print(letter_fdc)

In [61]:
# create df
# for mint condition
df_mint_condition = pd.DataFrame({'Mint_Condition': unique_mint_condition, 'Mint_Condition_Float': unique_mint_condition_as_float})
# for unused
df_unused = pd.DataFrame({'Unused': unique_unused, 'Unused_Float': unique_unused_as_float})
# for used
df_used = pd.DataFrame({'Used': unique_used, 'Used_Float': unique_used_as_float})
# for letter fdc
df_letter_fdc = pd.DataFrame({'Letter/FDC': unique_letter_fdc, 'Letter/FDC_Float': unique_letter_fdc_as_float})

df_merged_5 = pd.merge(df_merged_4, df_mint_condition, on='Mint_Condition', how='left')
df_merged_6 = pd.merge(df_merged_5, df_unused, on='Unused', how='left')
df_merged_7 = pd.merge(df_merged_6, df_used, on='Used', how='left')
df_merged_8 = pd.merge(df_merged_7, df_letter_fdc, on='Letter/FDC', how='left')

In [62]:
df_merged_8.iloc[0]

Country                                                            Aaland
Category                                                  Franking labels
Year                                                                 1984
Set_Url                 https://www.stampworld.com/stamps/Aaland/Frank...
Set_Name                                              1984 Franking Label
Set_ID                                                             256031
Set_Description            29. October WM: None Perforation: Imperforated
Number                                                                  1
Type                                                                    A
Denomination                                                     10-9890P
Color                                                        brownish red
Description                                                           NaN
Stamps_Issued                                                         NaN
Mint_Condition                        

# Currency

In [64]:
# list all unique values in Perforation column
unique_currencies = df_copy['Currency'].unique()
# print ALL unique values
for currency in unique_currencies:
    print(currency)

EUR


# Sheet_Size

In [86]:
# list all unique values in Sheet_Size column
unique_sheet_sizes = df_copy['Sheet_Size'].unique()
# to str
unique_sheet_sizes = [str(sheet_size) for sheet_size in unique_sheet_sizes]
# print ALL unique values
for sheet_size in unique_sheet_sizes:
    print(sheet_size)

nan
100.0
40.0
20.0
4.0
8.0
1.0
10.0
32.0
30.0
9.0
36.0
3.0
24.0
2.0
15.0
16.0
12.0
18.0
28.0
7.0
48.0
6.0
14.0
50.0
80.0
60.0
45.0
5.0
0.0
25.0
42.0
225.0
7247454554.0
13.0
21.0
81.0
8.0
2.0
4.0
6.0
1.0
3.0
5.0
14.0
0.0
13.0
50.0
20.0
16.0
40.0
10.0
15.0
30.0
25.0
48.0
32.0
36.0
9.0
12.0
24.0
7.0
100.0
17.0
107.0
11.0
10
5
4
50
2
40
1
25
20
3
6
8
64
100
120
150
14 x 13¾
9
70.0
56.0
64.0
150.0
90.0
99.0
98.0
91.0
42.0
18.0
28.0
49.0
120.0
88.0
110.0
156.0
200.0
108.0
160.0
80.0
52.0
70
30
45
60
240
80
Full Sheet
36
15
98
16
12
78
48
18
89
24
42
7
21.0
89.0
75.0
199.0
35.0
80 (4d) or 240 (others)
32
60.0
999999.0
120.0
75.0
23.0
240.0
256.0
96.0
200.0
54.0
64.0
11.0
29.0
35.0
17.0
19.0
90.0
565.0
88.0
112.0
456.0
77.0
222.0
55.0
34.0
22.0
70.0
150.0
84.0
142.0
96
480
56
112
240 (½d-3d, 5d, 6d and 1s), 80 (4d and 4½d, 9d) and 96 (10d)
200
28
11
500
50 (10x5)
70 (7x10)
50 (5x10)
72.0
56.0
27.0
63.0
320.0
128.0
439.0
26.0
108.0
300.0
33.0
500.0
1000.0
38.0
41.0
47.0
105.0
89.0
98.0
95.0
78

In [115]:
pattern1 = r"^\d+(\.\d+)?$"
pattern2 = r"^\d+(\.\d+)?( )?x( )?\d+(\.\d+)?$"
pattern3 = r"^\d+(\.\d+)?( )?\(( )?\d+(\.\d+)?( )?x( )?\d+(\.\d+)?( )?\)$"

unique_sheet_sizes_amount = []
unique_sheet_sizes_x = []
unique_sheet_sizes_y = []
unique_sheet_sizes_note = []

for sheet_size in unique_sheet_sizes:

    sheet_size = str(sheet_size)

    # replace ¾ with .75
    sheet_size = sheet_size.replace('¾', '.75')
    sheet_size = sheet_size.replace('stamps', '')

    sheet_size = sheet_size.strip()

    if sheet_size == "Full Sheet":
        print(sheet_size)
        unique_sheet_sizes_amount.append(None)
        unique_sheet_sizes_x.append(None)
        unique_sheet_sizes_y.append(None)
        unique_sheet_sizes_note.append("Full Sheet")
        continue

    if sheet_size == "nan" or sheet_size == "7247454554.0":
        unique_sheet_sizes_amount.append(None)
        unique_sheet_sizes_x.append(None)
        unique_sheet_sizes_y.append(None)
        unique_sheet_sizes_note.append(None)
        continue

    # if pattern1 matches
    if re.fullmatch(pattern1, sheet_size):
        # convert to float
        sheet_size = float(sheet_size)
        unique_sheet_sizes_amount.append(sheet_size)
        unique_sheet_sizes_x.append(None)
        unique_sheet_sizes_y.append(None)
        unique_sheet_sizes_note.append(None)
        continue

    # if pattern2 matches
    if re.fullmatch(pattern2, sheet_size):
        # split at x
        splitted = sheet_size.split('x')
        unique_sheet_sizes_amount.append(float(splitted[0].strip()) * float(splitted[1].strip()))
        unique_sheet_sizes_x.append(float(splitted[0].strip()))
        unique_sheet_sizes_y.append(float(splitted[1].strip()))
        unique_sheet_sizes_note.append(None)
        continue

    # if pattern3 matches
    if re.fullmatch(pattern3, sheet_size):
        # this time it looks like 4(2x3)
        # remove )
        sheet_size = sheet_size.replace(')', '')
        # split at x
        splitted = sheet_size.split('x')
        # split at (
        splitted2 = splitted[0].split('(')
        unique_sheet_sizes_amount.append(float(splitted2[0].strip()))
        unique_sheet_sizes_x.append(float(splitted2[1].strip()))
        unique_sheet_sizes_y.append(float(splitted[1].strip()))
        unique_sheet_sizes_note.append(None)
        continue

    unique_sheet_sizes_amount.append(None)
    unique_sheet_sizes_x.append(None)
    unique_sheet_sizes_y.append(None)
    unique_sheet_sizes_note.append("nothing matched")
    # unique_sheet_sizes_note.append(sheet_size)

# make df
df_sheet_sizes = pd.DataFrame({'Sheet_Size': unique_sheet_sizes, 'Sheet_Size_Amount': unique_sheet_sizes_amount, 'Sheet_Size_X': unique_sheet_sizes_x, 'Sheet_Size_Y': unique_sheet_sizes_y, 'Sheet_Size_Note': unique_sheet_sizes_note})

# Set display option to show all rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)  # Prevents wrapping of columns

print(df_sheet_sizes)

# Reset display option to default
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')
pd.reset_option('display.expand_frame_repr')

Full Sheet
                                            Sheet_Size  Sheet_Size_Amount  Sheet_Size_X  Sheet_Size_Y  Sheet_Size_Note
0                                                  nan                NaN           NaN           NaN             None
1                                                100.0              100.0           NaN           NaN             None
2                                                 40.0               40.0           NaN           NaN             None
3                                                 20.0               20.0           NaN           NaN             None
4                                                  4.0                4.0           NaN           NaN             None
5                                                  8.0                8.0           NaN           NaN             None
6                                                  1.0                1.0           NaN           NaN             None
7                                    

In [79]:
# find the row where Sheet_Size includes "7247454554.0"
df_copy['Sheet_Size'] = df_copy['Sheet_Size'].astype(str)
result = df_copy[df_copy['Sheet_Size'].fillna('').str.contains('7247454554.0', na=False)]
if not result.empty:
	print(result["Set_Url"].iloc[1])
else:
	print("No matching rows found")

https://www.stampworld.com/stamps/Algeria/Postage-stamps/g1965//


In [116]:
# merge with df_merged_8
df_merged_9 = pd.merge(df_merged_8, df_sheet_sizes, on='Sheet_Size', how='left')

In [117]:
# list proportion of "nothing matched" in Sheet_Size_Note column
count_nothing_matched = np.count_nonzero(df_merged_9['Sheet_Size_Note'] == "nothing matched")
print(count_nothing_matched)
print(count_nothing_matched / df_merged_9.shape[0])

441
0.0003982034792690393


In [113]:
df_merged_9.iloc[0]

Country                                                            Aaland
Category                                                  Franking labels
Year                                                                 1984
Set_Url                 https://www.stampworld.com/stamps/Aaland/Frank...
Set_Name                                              1984 Franking Label
Set_ID                                                             256031
Set_Description            29. October WM: None Perforation: Imperforated
Number                                                                  1
Type                                                                    A
Denomination                                                     10-9890P
Color                                                        brownish red
Description                                                           NaN
Stamps_Issued                                                         NaN
Mint_Condition                        

# Height_Width

In [ ]:
# list all unique values in Sheet_Size column
unique_height_width = df_copy['Height_Width'].unique()
# to str
unique_height_width = [str(sheet_size) for sheet_size in unique_height_width]
# print ALL unique values
for height_width in unique_height_width:
    print(height_width)

nan
24.0 X 34.0 mm
29.1 X 35.7 mm
26.0 X 34.0 mm
36.0 X 26.0 mm
25.0 X 37.0 mm
35.4 X 26.0 mm
35.9 X 25.7 mm
39.5 X 25.7 mm
26.0 X 35.0 mm
25.7 X 35.9 mm
35.0 X 26.0 mm
36.0 X 29.0 mm
31.0 X 36.0 mm
36.0 X 32.0 mm
51.0 X 21.0 mm
36.0 X 27.0 mm
30.0 X 36.0 mm
36.0 X 30.0 mm
25.0 X 36.0 mm
32.0 X 37.0 mm
40.0 X 26.0 mm
25.0 X 39.0 mm
12.0 X 50.0 mm
37.0 X 27.0 mm
30.0 X 38.0 mm
31.0 X 37.0 mm
30.0 X 40.0 mm
35.0 X 25.0 mm
30.0 X 35.0 mm
37.0 X 32.0 mm
36.0 X 25.0 mm
32.0 X 36.0 mm
52.0 X 36.0 mm
37.0 X 31.0 mm
30.0 X 41.0 mm
38.0 X 38.0 mm
30.0 X 46.0 mm
24.0 X 52.0 mm
54.0 X 24.0 mm
26.0 X 36.0 mm
31.0 X 40.0 mm
38.0 X 35.0 mm
42.0 X 36.0 mm
27.0 X 40.0 mm
29.0 X 38.0 mm
33.0 X 33.0 mm
46.0 X 30.0 mm
32.0 X 39.0 mm
35.0 X 35.0 mm
72.0 X 29.0 mm
52.0 X 34.0 mm
43.0 X 29.0 mm
70.0 X 105.0 mm
36.0 X 36.0 mm
26.0 X 26.0 mm
29.0 X 42.0 mm
27.0 X 42.0 mm
52.0 X 24.0 mm
39.0 X 30.0 mm
36.3 X 31.5 mm
35.0 X 26.6 mm
40.0 X 25.5 mm
40.3 X 26.1 mm
26.1 X 40.3 mm
31.5 X 36.3 mm
36.0 X 26.1 mm
52.0 

In [126]:
pattern1 = r"^\d+(\.\d+)?( )?X( )?\d+(\.\d+)? mm$"
pattern2 = r"None X( )?\d+(\.\d+)? mm$"

height = []
width = []

for height_width in unique_height_width:
    
    height_width = str(height_width)

    # replace 2.0 X -4.0 mm with nan
    height_width = height_width.replace('2.0 X -4.0 mm', 'nan')

    if height_width == "nan":
        height.append(None)
        width.append(None)
        continue

    # if pattern1 matches
    if re.fullmatch(pattern1, height_width):
        # remove mm
        height_width = height_width.replace('mm', '').strip()
        # split at x
        splitted = height_width.split('X')
        height.append(float(splitted[0].strip()))
        width.append(float(splitted[1].strip()))
        continue

    # if pattern2 matches
    if re.fullmatch(pattern2, height_width):
        # remove mm
        height_width = height_width.replace('mm', '').strip()
        # split at x
        splitted = height_width.split('X')
        height.append(None)
        width.append(float(splitted[1].strip()))
        continue

    height.append(None)
    width.append(None)

# make df
df_height_width = pd.DataFrame({'Height_Width': unique_height_width, 'Height': height, 'Width': width})

# Set display option to show all rows
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.expand_frame_repr', False)  # Prevents wrapping of columns

print(df_height_width)

# Reset display option to default
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')
pd.reset_option('display.expand_frame_repr')

            Height_Width  Height   Width
0                    nan     NaN     NaN
1         24.0 X 34.0 mm    24.0    34.0
2         29.1 X 35.7 mm    29.1    35.7
3         26.0 X 34.0 mm    26.0    34.0
4         36.0 X 26.0 mm    36.0    26.0
5         25.0 X 37.0 mm    25.0    37.0
6         35.4 X 26.0 mm    35.4    26.0
7         35.9 X 25.7 mm    35.9    25.7
8         39.5 X 25.7 mm    39.5    25.7
9         26.0 X 35.0 mm    26.0    35.0
10        25.7 X 35.9 mm    25.7    35.9
11        35.0 X 26.0 mm    35.0    26.0
12        36.0 X 29.0 mm    36.0    29.0
13        31.0 X 36.0 mm    31.0    36.0
14        36.0 X 32.0 mm    36.0    32.0
15        51.0 X 21.0 mm    51.0    21.0
16        36.0 X 27.0 mm    36.0    27.0
17        30.0 X 36.0 mm    30.0    36.0
18        36.0 X 30.0 mm    36.0    30.0
19        25.0 X 36.0 mm    25.0    36.0
20        32.0 X 37.0 mm    32.0    37.0
21        40.0 X 26.0 mm    40.0    26.0
22        25.0 X 39.0 mm    25.0    39.0
23        12.0 X

In [125]:
# find the row where Stamps_Issued includes "0.911.000 "
df_copy[df_copy['Height_Width'].fillna('').str.contains('2.0 X -4.0 mm', regex = False)]["Set_Url"].iloc[0]

'https://www.stampworld.com/stamps/Sierra-Leone/Postage-stamps/g2155//'

In [127]:
# merge with df_merged_9
df_merged_10 = pd.merge(df_merged_9, df_height_width, on='Height_Width', how='left')

In [128]:
df_merged_10.iloc[0]

Country                                                            Aaland
Category                                                  Franking labels
Year                                                                 1984
Set_Url                 https://www.stampworld.com/stamps/Aaland/Frank...
Set_Name                                              1984 Franking Label
Set_ID                                                             256031
Set_Description            29. October WM: None Perforation: Imperforated
Number                                                                  1
Type                                                                    A
Denomination                                                     10-9890P
Color                                                        brownish red
Description                                                           NaN
Stamps_Issued                                                         NaN
Mint_Condition                        